In [127]:
import pandas as pd
import numpy as np
import math
import keras
from scipy.stats import norm
import keras.backend as K
from keras.models import Sequential
from keras.layers import Dense
from keras.callbacks import EarlyStopping
import keras.optimizers as opt
import time
import sys

In [128]:
no_of_paths = 50000
no_of_hidden_nodes = 64
s_0 = 1

w_dict = {}
no_of_output_nodes = 1
weights_dict = {}
no_of_assets = 5

# cor_mat = np.ones((no_of_assets, no_of_assets), dtype=np.float64)
cor_mat = [[1.0, 0.79, 0.82, 0.91, 0.84],
           [0.79, 1.0, 0.73, 0.80, 0.76],
           [0.82, 0.73, 1.0, 0.77, 0.72],
           [0.91, 0.80, 0.77, 1.0, 0.90],
           [0.84, 0.76, 0.72, 0.90, 1.0]]

#vol_list = np.array([0.518, 0.648])
vol_list = np.array([0.518, 0.648, 0.623, 0.570, 0.530])

Notional = 100
curr_stock_price = np.ones(no_of_assets) * s_0
t = 1
k = 1
no_of_exercise_days = 10
r = 0.05
#w = np.array([0.4, 0.6])
w = np.array([0.381, 0.065, 0.057, 0.270, 0.227])

w = w.reshape(-1, 1)
exercise_days = np.array([float(i / no_of_exercise_days) for i in range(1, no_of_exercise_days + 1)])
dt = t / no_of_exercise_days

In [129]:
def generate_covariance_from_correlation(cor_mat, vol_list, dt):
    vol_diag_mat = np.diag(vol_list)
    cov_mat = np.dot(np.dot(vol_diag_mat, cor_mat), vol_diag_mat) * dt
    return cov_mat

In [130]:
def multi_variate_gbm_simulation(no_of_paths, no_of_exercise_days, exercise_days, no_of_assets,
                                 curr_stock_price, r, vol_list, cov_mat, t):
    zero_mean = np.zeros(no_of_assets)

    dw_mat = np.random.multivariate_normal(zero_mean, cov_mat, (no_of_paths, no_of_exercise_days))
    dt = t / no_of_exercise_days

    sim_ln_stock_mat = np.zeros((no_of_paths, no_of_exercise_days + 1, no_of_assets))
    sim_ln_stock_mat[:, 0] = np.tile(np.log(curr_stock_price), (no_of_paths, 1))
    base_drift = np.tile((np.add(np.full(no_of_assets, r), - 0.5 * np.square(vol_list))), (no_of_paths, 1)) * dt

    for day in range(1, no_of_exercise_days + 1):
        curr_drift = sim_ln_stock_mat[:, day - 1] + base_drift
        sim_ln_stock_mat[:, day] = curr_drift + dw_mat[:, day - 1]

    sim_stock_mat = np.exp(sim_ln_stock_mat)
    return sim_stock_mat

In [131]:
def duplicates(lst, item):
    return [i for i, x in enumerate(lst) if x == item]


# Generate covariance matrix without considering dt
cov_mat = generate_covariance_from_correlation(cor_mat, vol_list, dt)

In [132]:
def pricer_sgbm(no_of_paths, no_of_exercise_days, exercise_days, no_of_assets, w, sim_stock_mat):

    continuation_value = np.zeros((no_of_paths, 1))
    stock_vec = sim_stock_mat[:, no_of_exercise_days]
    intrinsic_value = np.maximum(k - np.dot(stock_vec, w), 0)
    continuation_value = intrinsic_value

In [133]:
def pricer_arithmetic_pre(no_of_paths, no_of_exercise_days, exercise_days, no_of_assets, w, sim_stock_mat,
                          batch_size, no_of_epochs, no_of_hidden_nodes, no_of_output_nodes, t, model):

    continuation_value = np.zeros((no_of_paths, 1))
    stock_vec = sim_stock_mat[:, no_of_exercise_days]
    intrinsic_value = np.maximum(k - np.dot(stock_vec, w), 0)
    continuation_value = intrinsic_value
    
    # Finding intrinsic value of the option for all paths and exercise days
    for day in range(no_of_exercise_days - 1, no_of_exercise_days - 2, -1):
        stock_vec = sim_stock_mat[:, day + 1]
        option_value = continuation_value

        X_train = np.log(stock_vec)
        X_train = X_train.reshape(-1, no_of_assets)
        Y_train = option_value
        Y_train = np.asarray(Y_train)
        Y_train.reshape(-1, 1, 1)

        nnet_output = model.fit(X_train, Y_train, epochs=no_of_epochs[day], batch_size=batch_size, verbose=0,
                                validation_split=0.2, callbacks=[es])

        w_vect = np.array(nnet_model.layers[0].get_weights()[0])
        w_vect_2 = np.array(nnet_model.layers[1].get_weights()[0])
        strikes = np.array(nnet_model.layers[0].get_weights()[1])
        bias_2 = np.array(nnet_model.layers[1].get_weights()[1])
        strikes = np.asarray(strikes)

        stock_vec = sim_stock_mat[:, day]
        x = np.log(stock_vec) + np.tile(((r - 0.5 * np.square(vol_list)) * dt).reshape(1, no_of_assets),
                                        (no_of_paths, 1))
        opt_val = np.zeros((no_of_paths, 1))

        for node in range(0, no_of_hidden_nodes):
            w_o = w_vect[:, node]
            w_o = w_o.reshape(no_of_assets, 1)
            mu = np.dot(x, w_o) + strikes[node]
            var = np.dot(np.dot(w_o.T, cov_mat), w_o)
            sd = var ** 0.5
            ft = mu * (1 - norm(0, sd).cdf(-mu))
            st = (sd / (2 * math.pi) ** 0.5) * np.exp(-0.5 * (mu / sd) ** 2)
            opt_val = opt_val + w_vect_2[node] * (ft + st)

        continuation_value = (opt_val + bias_2) * np.exp(-r * dt)

    return model


In [134]:
def pricer_bermudan_options_by_nn(no_of_paths, no_of_exercise_days, exercise_days, no_of_assets, w, sim_stock_mat,
                                  batch_size, no_of_epochs, no_of_hidden_nodes, no_of_output_nodes, t, nnet_model):
    # Creating zero n-d arrays for intrinsic value, continuation value and option value
    continuation_value = np.zeros((no_of_paths, 1))
    stock_vec = sim_stock_mat[:, no_of_exercise_days]
    intrinsic_value = np.maximum(k - np.dot(stock_vec, w), 0)
    continuation_value = intrinsic_value
    
    for day in range(no_of_exercise_days - 1, -1, -1):
        stock_vec = sim_stock_mat[:, day + 1]
        

        option_value = continuation_value

        X_train = np.log(stock_vec)
        X_train = X_train.reshape(-1, no_of_assets)
        Y_train = option_value
        Y_train = np.asarray(Y_train)
        Y_train.reshape(-1, 1, 1)

        nnet_output = nnet_model.fit(X_train, Y_train, epochs=no_of_epochs[day], batch_size=batch_size, verbose=1,
                                validation_split=0.2, callbacks=[es])

        w1 = nnet_model.layers[0].get_weights()
        w2 = nnet_model.layers[1].get_weights()
        w_dict[day] = ([w1, w2])
        w_vect = np.array(nnet_model.layers[0].get_weights()[0])
        w_vect_2 = np.array(nnet_model.layers[1].get_weights()[0])
        strikes = np.array(nnet_model.layers[0].get_weights()[1])
        bias_2 = np.array(nnet_model.layers[1].get_weights()[1])
        strikes = np.asarray(strikes)
        weights_dict[day] = ([nnet_model.layers[0].get_weights()[0], nnet_model.layers[1].get_weights()[0],
                              nnet_model.layers[0].get_weights()[1], nnet_model.layers[1].get_weights()[1]])
        stock_vec = sim_stock_mat[:, day]
        x = np.log(stock_vec) + np.tile(((r - 0.5 * np.square(vol_list)) * dt).reshape(1, no_of_assets),
                                        (no_of_paths, 1))
        opt_val = np.zeros((no_of_paths, 1))

        for node in range(0, no_of_hidden_nodes):
            w_o = w_vect[:, node]
            w_o = w_o.reshape(no_of_assets, 1)
            mu = np.dot(x, w_o) + strikes[node]
            var = np.dot(np.dot(w_o.T, cov_mat), w_o)
            sd = var ** 0.5
            ft = mu * (1 - norm(0, sd).cdf(-mu))
            st = (sd / (2 * math.pi) ** 0.5) * np.exp(-0.5 * (mu / sd) ** 2)
            opt_val = opt_val + w_vect_2[node] * (ft + st)

        continuation_value = (opt_val + bias_2) * np.exp(-r * dt)

    return (np.mean(continuation_value))

In [135]:
price_list = []
for i in range(0, 30):
    
    sim_stock_mat = multi_variate_gbm_simulation(no_of_paths, no_of_exercise_days, exercise_days, no_of_assets,
                                                 curr_stock_price, r, vol_list, cov_mat, t)
    batch_size = int(no_of_paths / 10)
    no_of_epochs = np.array([100, 100, 100, 500, 500, 500, 500, 2000, 2000, 2000])

    nnet_model = Sequential()
    nnet_model.add(Dense(no_of_hidden_nodes, activation='relu', kernel_initializer='random_uniform'))
    nnet_model.add(Dense(1, activation='linear', kernel_initializer='normal'))
    nnet_model.compile(optimizer=opt.Adam(lr=0.001), loss='mean_squared_error')
    es = EarlyStopping(monitor='val_loss', mode='min', patience=5)

    nnet_model = pricer_arithmetic_pre(no_of_paths, no_of_exercise_days, exercise_days, no_of_assets, w, sim_stock_mat,
                                       batch_size, no_of_epochs, no_of_hidden_nodes, no_of_output_nodes, t, nnet_model)
    K.set_value(nnet_model.optimizer.lr, 5e-4)

    sim_stock_mat = multi_variate_gbm_simulation(no_of_paths, no_of_exercise_days, exercise_days, no_of_assets,
                                                 curr_stock_price, r, vol_list, cov_mat, t)

    nnet_model = pricer_arithmetic_pre(no_of_paths, no_of_exercise_days, exercise_days, no_of_assets, w, sim_stock_mat,
                                      batch_size, no_of_epochs, no_of_hidden_nodes, no_of_output_nodes, t, nnet_model)

    K.set_value(nnet_model.optimizer.lr, 1e-3)

    price = pricer_bermudan_options_by_nn(no_of_paths, no_of_exercise_days, exercise_days, no_of_assets, w, sim_stock_mat,
                                          batch_size, no_of_epochs, no_of_hidden_nodes, no_of_output_nodes, t, nnet_model)

    price_list.append(price)
    
df = pd.DataFrame({'Runs:' + str(no_of_paths):price_list})
# df.to_csv('df_pv_comonotonic_nn_nodes_' + str(no_of_hidden_nodes) + '_sim' + str(no_of_paths) + '.csv')
print(df)
# text_file = open('European_Arithmetic.txt', "a")
# strx = "\n Paths: "+ str(no_of_paths)+", Nodes: "+str(no_of_hidden_nodes)+", Price: " + str(price*Notional)
# text_file.write(strx)
# text_file.close()

Epoch 1/2000
8/8 [==============================] - 0s 20ms/step - loss: 9.3204e-06 - val_loss: 1.6807e-05
Epoch 2/2000
8/8 [==============================] - 0s 7ms/step - loss: 1.1312e-05 - val_loss: 1.0051e-05
Epoch 3/2000
8/8 [==============================] - 0s 3ms/step - loss: 9.4866e-06 - val_loss: 1.0105e-05
Epoch 4/2000
8/8 [==============================] - 0s 3ms/step - loss: 8.9807e-06 - val_loss: 9.6836e-06
Epoch 5/2000
8/8 [==============================] - 0s 4ms/step - loss: 8.7981e-06 - val_loss: 9.3739e-06
Epoch 6/2000
8/8 [==============================] - 0s 4ms/step - loss: 8.6680e-06 - val_loss: 9.4311e-06
Epoch 7/2000
8/8 [==============================] - 0s 3ms/step - loss: 8.6086e-06 - val_loss: 9.2946e-06
Epoch 8/2000
8/8 [==============================] - 0s 4ms/step - loss: 8.5572e-06 - val_loss: 9.2472e-06
Epoch 9/2000
8/8 [==============================] - 0s 3ms/step - loss: 8.5209e-06 - val_loss: 9.3579e-06
Epoch 10/2000
8/8 [==========================

Epoch 1/2000
8/8 [==============================] - 0s 11ms/step - loss: 1.0025e-04 - val_loss: 2.2585e-04
Epoch 2/2000
8/8 [==============================] - 0s 7ms/step - loss: 9.3010e-05 - val_loss: 2.0798e-05
Epoch 3/2000
8/8 [==============================] - 0s 9ms/step - loss: 3.5859e-05 - val_loss: 8.9599e-06
Epoch 4/2000
8/8 [==============================] - 0s 3ms/step - loss: 1.9391e-05 - val_loss: 9.2249e-06
Epoch 5/2000
8/8 [==============================] - 0s 3ms/step - loss: 1.3070e-05 - val_loss: 9.5413e-06
Epoch 6/2000
8/8 [==============================] - 0s 3ms/step - loss: 1.0417e-05 - val_loss: 9.3149e-06
Epoch 7/2000
8/8 [==============================] - 0s 4ms/step - loss: 9.3156e-06 - val_loss: 9.1190e-06
Epoch 8/2000
8/8 [==============================] - 0s 3ms/step - loss: 8.7952e-06 - val_loss: 9.0222e-06
Epoch 1/2000
8/8 [==============================] - 0s 21ms/step - loss: 2.2062e-04 - val_loss: 1.6645e-04
Epoch 2/2000
8/8 [==========================

Epoch 1/2000
8/8 [==============================] - 0s 15ms/step - loss: 3.9599e-05 - val_loss: 9.3396e-05
Epoch 2/2000
8/8 [==============================] - 0s 8ms/step - loss: 4.2860e-05 - val_loss: 2.2101e-05
Epoch 3/2000
8/8 [==============================] - 0s 5ms/step - loss: 2.2110e-05 - val_loss: 2.0916e-05
Epoch 4/2000
8/8 [==============================] - 0s 3ms/step - loss: 1.5862e-05 - val_loss: 1.0633e-05
Epoch 5/2000
8/8 [==============================] - 0s 3ms/step - loss: 1.2174e-05 - val_loss: 1.3126e-05
Epoch 6/2000
8/8 [==============================] - 0s 4ms/step - loss: 1.0975e-05 - val_loss: 1.0891e-05
Epoch 7/2000
8/8 [==============================] - 0s 3ms/step - loss: 1.0235e-05 - val_loss: 1.0229e-05
Epoch 8/2000
8/8 [==============================] - 0s 3ms/step - loss: 9.9390e-06 - val_loss: 1.0353e-05
Epoch 9/2000
8/8 [==============================] - 0s 3ms/step - loss: 9.8044e-06 - val_loss: 1.0319e-05
Epoch 10/2000
8/8 [==========================

Epoch 1/2000
8/8 [==============================] - 0s 12ms/step - loss: 2.7551e-05 - val_loss: 7.3668e-05
Epoch 2/2000
8/8 [==============================] - 0s 6ms/step - loss: 3.2520e-05 - val_loss: 3.3003e-05
Epoch 3/2000
8/8 [==============================] - 0s 7ms/step - loss: 1.7491e-05 - val_loss: 1.1871e-05
Epoch 4/2000
8/8 [==============================] - 0s 3ms/step - loss: 1.1358e-05 - val_loss: 9.3251e-06
Epoch 5/2000
8/8 [==============================] - 0s 3ms/step - loss: 9.1845e-06 - val_loss: 9.5333e-06
Epoch 6/2000
8/8 [==============================] - 0s 3ms/step - loss: 8.7396e-06 - val_loss: 8.0661e-06
Epoch 7/2000
8/8 [==============================] - 0s 3ms/step - loss: 8.1431e-06 - val_loss: 8.2738e-06
Epoch 8/2000
8/8 [==============================] - 0s 3ms/step - loss: 7.8605e-06 - val_loss: 7.9224e-06
Epoch 9/2000
8/8 [==============================] - 0s 3ms/step - loss: 7.7326e-06 - val_loss: 7.8749e-06
Epoch 10/2000
8/8 [==========================

Epoch 1/2000
8/8 [==============================] - 0s 16ms/step - loss: 5.4969e-05 - val_loss: 1.8721e-04
Epoch 2/2000
8/8 [==============================] - 0s 7ms/step - loss: 8.4016e-05 - val_loss: 2.6757e-05
Epoch 3/2000
8/8 [==============================] - 0s 5ms/step - loss: 3.5629e-05 - val_loss: 1.5291e-05
Epoch 4/2000
8/8 [==============================] - 0s 3ms/step - loss: 1.9828e-05 - val_loss: 1.2734e-05
Epoch 5/2000
8/8 [==============================] - 0s 3ms/step - loss: 1.3268e-05 - val_loss: 1.0900e-05
Epoch 6/2000
8/8 [==============================] - 0s 3ms/step - loss: 1.0566e-05 - val_loss: 9.7450e-06
Epoch 7/2000
8/8 [==============================] - 0s 3ms/step - loss: 9.2612e-06 - val_loss: 9.0579e-06
Epoch 8/2000
8/8 [==============================] - 0s 3ms/step - loss: 8.5929e-06 - val_loss: 8.4106e-06
Epoch 9/2000
8/8 [==============================] - 0s 3ms/step - loss: 8.4159e-06 - val_loss: 8.4246e-06
Epoch 10/2000
8/8 [==========================

...

Epoch 1/2000
8/8 [==============================] - 0s 16ms/step - loss: 1.1328e-05 - val_loss: 1.1961e-05
Epoch 2/2000
8/8 [==============================] - 0s 6ms/step - loss: 1.1252e-05 - val_loss: 1.1881e-05
Epoch 3/2000
8/8 [==============================] - 0s 5ms/step - loss: 1.1187e-05 - val_loss: 1.1932e-05
Epoch 4/2000
8/8 [==============================] - 0s 4ms/step - loss: 1.1236e-05 - val_loss: 1.1777e-05
Epoch 5/2000
8/8 [==============================] - 0s 4ms/step - loss: 1.1225e-05 - val_loss: 1.2049e-05
Epoch 6/2000
8/8 [==============================] - 0s 6ms/step - loss: 1.1159e-05 - val_loss: 1.1723e-05
Epoch 7/2000
8/8 [==============================] - 0s 4ms/step - loss: 1.1093e-05 - val_loss: 1.1634e-05
Epoch 8/2000
8/8 [==============================] - 0s 7ms/step - loss: 1.1078e-05 - val_loss: 1.1707e-05
Epoch 9/2000
8/8 [==============================] - 0s 5ms/step - loss: 1.1134e-05 - val_loss: 1.1759e-05
Epoch 10/2000
8/8 [==========================

Epoch 1/2000
8/8 [==============================] - 0s 15ms/step - loss: 9.9309e-06 - val_loss: 1.1499e-05
Epoch 2/2000
8/8 [==============================] - 0s 7ms/step - loss: 1.0583e-05 - val_loss: 1.1276e-05
Epoch 3/2000
8/8 [==============================] - 0s 4ms/step - loss: 1.0112e-05 - val_loss: 9.2864e-06
Epoch 4/2000
8/8 [==============================] - 0s 4ms/step - loss: 9.4487e-06 - val_loss: 9.2852e-06
Epoch 5/2000
8/8 [==============================] - 0s 3ms/step - loss: 9.2734e-06 - val_loss: 9.3205e-06
Epoch 6/2000
8/8 [==============================] - 0s 4ms/step - loss: 9.2985e-06 - val_loss: 9.2279e-06
Epoch 7/2000
8/8 [==============================] - 0s 4ms/step - loss: 9.3212e-06 - val_loss: 9.2947e-06
Epoch 8/2000
8/8 [==============================] - 0s 4ms/step - loss: 9.2793e-06 - val_loss: 9.2274e-06
Epoch 9/2000
8/8 [==============================] - 0s 4ms/step - loss: 9.2650e-06 - val_loss: 9.4366e-06
Epoch 10/2000
8/8 [==========================

Epoch 1/2000
8/8 [==============================] - 0s 13ms/step - loss: 4.9857e-05 - val_loss: 1.1038e-04
Epoch 2/2000
8/8 [==============================] - 0s 9ms/step - loss: 4.6513e-05 - val_loss: 2.8628e-05
Epoch 3/2000
8/8 [==============================] - 0s 7ms/step - loss: 2.1339e-05 - val_loss: 1.8513e-05
Epoch 4/2000
8/8 [==============================] - 0s 4ms/step - loss: 1.4590e-05 - val_loss: 1.5176e-05
Epoch 5/2000
8/8 [==============================] - 0s 3ms/step - loss: 1.1369e-05 - val_loss: 1.1992e-05
Epoch 6/2000
8/8 [==============================] - 0s 4ms/step - loss: 9.4672e-06 - val_loss: 9.4927e-06
Epoch 7/2000
8/8 [==============================] - 0s 4ms/step - loss: 8.6480e-06 - val_loss: 8.3970e-06
Epoch 8/2000
8/8 [==============================] - 0s 3ms/step - loss: 8.2771e-06 - val_loss: 8.0166e-06
Epoch 9/2000
8/8 [==============================] - 0s 4ms/step - loss: 8.1008e-06 - val_loss: 7.9345e-06
Epoch 10/2000
8/8 [==========================

Epoch 1/2000
8/8 [==============================] - 0s 12ms/step - loss: 6.0874e-05 - val_loss: 1.3154e-05
Epoch 2/2000
8/8 [==============================] - 0s 7ms/step - loss: 4.6747e-05 - val_loss: 2.9122e-05
Epoch 3/2000
8/8 [==============================] - 0s 5ms/step - loss: 2.3675e-05 - val_loss: 1.9864e-05
Epoch 4/2000
8/8 [==============================] - 0s 4ms/step - loss: 1.5210e-05 - val_loss: 1.2578e-05
Epoch 5/2000
8/8 [==============================] - 0s 3ms/step - loss: 1.1188e-05 - val_loss: 9.3326e-06
Epoch 6/2000
8/8 [==============================] - 0s 4ms/step - loss: 9.0618e-06 - val_loss: 8.3597e-06
Epoch 7/2000
8/8 [==============================] - 0s 4ms/step - loss: 8.1988e-06 - val_loss: 8.1252e-06
Epoch 8/2000
8/8 [==============================] - 0s 4ms/step - loss: 7.8955e-06 - val_loss: 8.0364e-06
Epoch 9/2000
8/8 [==============================] - 0s 4ms/step - loss: 7.8256e-06 - val_loss: 8.2172e-06
Epoch 10/2000
8/8 [==========================

Epoch 1/2000
8/8 [==============================] - 0s 25ms/step - loss: 9.3159e-06 - val_loss: 9.6360e-06
Epoch 2/2000
8/8 [==============================] - 0s 3ms/step - loss: 9.2950e-06 - val_loss: 9.5759e-06
Epoch 3/2000
8/8 [==============================] - 0s 4ms/step - loss: 9.3126e-06 - val_loss: 9.7579e-06
Epoch 4/2000
8/8 [==============================] - 0s 4ms/step - loss: 9.4008e-06 - val_loss: 9.5582e-06
Epoch 5/2000
8/8 [==============================] - 0s 4ms/step - loss: 9.2251e-06 - val_loss: 9.7618e-06
Epoch 6/2000
8/8 [==============================] - 0s 3ms/step - loss: 9.3173e-06 - val_loss: 9.6664e-06
Epoch 7/2000
8/8 [==============================] - 0s 4ms/step - loss: 9.2759e-06 - val_loss: 9.6204e-06
Epoch 8/2000
8/8 [==============================] - 0s 3ms/step - loss: 9.2573e-06 - val_loss: 9.5513e-06
Epoch 9/2000
8/8 [==============================] - 0s 4ms/step - loss: 9.3107e-06 - val_loss: 9.8237e-06
Epoch 10/2000
8/8 [==========================

In [257]:
import numpy as np
from numpy.polynomial import Polynomial

def ls_american_option_quadratic_iter(X, t, r, strike, w):
    # given no prior exercise we just receive the payoff of a European option
    cashflow = np.maximum(strike - np.dot(X[:,-1, :], w), 0.0)
    # iterating backwards in time
    for i in reversed(range(1, X.shape[1] - 2)):
        # discount factor between t[i] and t[i+1]
        df = np.exp(-r * (t[i + 1] - t[i]))
        # discount cashflows from next period
        cashflow = cashflow * df
        x = X[:, i, :]
        # exercise value for time t[i]
        exercise = np.maximum(strike - np.dot(x, w), 0.0)
        # boolean index of all in-the-money paths
        itm = exercise > 0
        itm_flattened = itm.flatten()
        # fit polynomial of degree 
        print(f"x[itm_flattened]: {x[itm_flattened].shape}")
        print(f"cashflow[itm_flattened]: {np.tile(cashflow[itm_flattened], (1,X.shape[2])).shape}")
        tiled_cashflow = np.tile(cashflow[itm_flattened], (1,X.shape[2]))

        poly = PolynomialFeatures(degree=2)

        fitted = Polynomial.fit(x[itm_flattened], tiled_cashflow, 2)
        # approximate continuation value
        continuation = fitted(x)
        # boolean index where exercise is beneficial
        ex_idx = itm & (exercise > continuation)
        # update cashflows with early exercises
        cashflow[ex_idx] = exercise[ex_idx]

        yield cashflow, x, fitted, continuation, exercise, ex_idx


def longstaff_schwartz_american_option_quadratic(X, t, r, strike, w):
    for cashflow, *_ in ls_american_option_quadratic_iter(X, t, r, strike, w):
        pass
    return cashflow.mean(axis=0) * np.exp(-r * (t[1] - t[0]))

In [258]:
exercise_days

array([0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1. ])

In [259]:
no_of_paths = 40000
s_0 = 1

no_of_assets = 5

# cor_mat = np.ones((no_of_assets, no_of_assets), dtype=np.float64)
# vol_list = np.array([0.2])

cor_mat = [[1.0, 0.79, 0.82, 0.91, 0.84],
           [0.79, 1.0, 0.73, 0.80, 0.76],
           [0.82, 0.73, 1.0, 0.77, 0.72],
           [0.91, 0.80, 0.77, 1.0, 0.90],
           [0.84, 0.76, 0.72, 0.90, 1.0]]

vol_list = np.array([0.518, 0.648, 0.623, 0.570, 0.530])

cov_mat = generate_covariance_from_correlation(cor_mat, vol_list, dt)

Notional = 40
curr_stock_price = np.ones(no_of_assets) * s_0
t = 1
k = 1

no_of_exercise_days = 10
r = 0.06
#w = np.array([1.0])
w = np.array([0.381, 0.065, 0.057, 0.270, 0.227])
w = w.reshape(-1, 1)

exercise_days = np.array([float(i / no_of_exercise_days) for i in range(1, no_of_exercise_days + 1)])
dt = t / no_of_exercise_days

X = multi_variate_gbm_simulation(no_of_paths, no_of_exercise_days, exercise_days, no_of_assets,
                                                 curr_stock_price, r, vol_list, cov_mat, t)

In [260]:
longstaff_schwartz_american_option_quadratic(X, exercise_days, r, k, w) * Notional

x[itm_flattened]: (21980, 5)
cashflow[itm_flattened]: (21980, 5)


ValueError: Coefficient array is not 1-d

In [ ]:
x = np.array([["a",1],["b",2],["c",3]])
y = np.array([2,3,54,5,7])
itm = y > 5
itm = np.array([True, False, True])
x[itm]
z = np.array([[1],[2],[3]])
z = z.flatten()
z

array([1, 2, 3])